In [1]:
# ============================================================================
# IMPORTS
# ============================================================================

import os
import gc
import json
import warnings
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import (
    accuracy_score,
    f1_score,
    precision_score,
    recall_score,
    classification_report,
    hamming_loss
)

from torch.optim import AdamW

from transformers import (
    AutoTokenizer,
    AutoModelForSequenceClassification,
    get_linear_schedule_with_warmup,
    LongformerTokenizer,
    LongformerForSequenceClassification,
    BigBirdTokenizer,
    BigBirdForSequenceClassification,
    BartTokenizer,
    BartForSequenceClassification,
    T5Tokenizer,
    T5ForConditionalGeneration,
    AutoModel
)


from sentence_transformers import SentenceTransformer
from tqdm.notebook import tqdm
from typing import Dict, List, Tuple, Optional
from dataclasses import dataclass

warnings.filterwarnings('ignore')

2025-10-04 15:54:39.586697: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1759593279.775259      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1759593279.826158      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [2]:
# ============================================================================
# EXPERIMENTAL SETUP AND HYPERPARAMETERS
# ============================================================================

@dataclass
class ExperimentConfig:
    """Configuration for experimental setup."""
    
    # Paths
    DATASET_PATH: str = "/kaggle/input/eacl-26-dataset-2/EACL_26-FinancialDiscussionsDataset.json"
    OUTPUT_DIR: str = "/kaggle/working"
    
    # Reproducibility
    RANDOM_SEED: int = 42
    
    # Data splits
    TRAIN_SIZE: float = 0.6
    VAL_SIZE: float = 0.2
    TEST_SIZE: float = 0.2
    
    # Training hyperparameters (following M-HELP)
    BATCH_SIZE: int = 16
    LEARNING_RATE: float = 5e-5
    NUM_EPOCHS: int = 10
    WEIGHT_DECAY: float = 1e-2
    WARMUP_STEPS: int = 500
    MAX_GRAD_NORM: float = 1.0
    
    # Early stopping
    EARLY_STOPPING_PATIENCE: int = 3
    
    # Optimizer parameters
    ADAM_BETA1: float = 0.9
    ADAM_BETA2: float = 0.999
    ADAM_EPSILON: float = 1e-8
    
    # Model-specific parameters
    DROPOUT: float = 0.2
    
    # Max sequence lengths per model type
    MAX_SEQ_LENGTH_STANDARD: int = 512
    MAX_SEQ_LENGTH_LONG: int = 1024
    
    # Label definitions
    INTENT_LABELS: List[str] = None
    IMPACT_LABELS: List[str] = None
    
    def __post_init__(self):
        """Initialize label lists after dataclass creation."""
        # PROJECT 2 LABELS
        self.INTENT_LABELS = [
            "Advocacy & Warning",
            "Community Building & Solidarity Seeking",
            "Emotional & Esteem Support-Seeking",
            "Informational Help-Seeking",
            "Instrumental Help-Seeking",
            "Sense-Making & Narrative Construction",
            "Venting / Catharsis"
        ]
        
        self.IMPACT_LABELS = [
            "Behavioral Impact (Maladaptive Coping)",
            "Cognitive Impact",
            "Economic & Material Impact",
            "Physical Health Impact",
            "Psychological & Emotional Impact",
            "Relational & Social Impact"
        ]

CONFIG = ExperimentConfig()

In [3]:
# ============================================================================
# UTILITY FUNCTIONS
# ============================================================================

def set_seed(seed: int) -> None:
    """Set random seed for reproducibility."""
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

def clear_memory() -> None:
    """Clear GPU and CPU memory."""
    gc.collect()
    torch.cuda.empty_cache()

def validate_dataset_structure(data: List[Dict]) -> None:
    """Validate dataset structure and raise errors for malformed data."""
    if not isinstance(data, list):
        raise ValueError(f"Dataset must be a list, got {type(data)}")
    
    if len(data) == 0:
        raise ValueError("Dataset is empty")
    
    required_keys = {'sample_id', 'text', 'labels'}
    for idx, sample in enumerate(data):
        missing_keys = required_keys - set(sample.keys())
        if missing_keys:
            raise ValueError(f"Sample {idx} missing keys: {missing_keys}")
        
        if not isinstance(sample['labels'], dict):
            raise ValueError(f"Sample {idx}: 'labels' must be dict, got {type(sample['labels'])}")
        
        if 'intent' not in sample['labels'] or 'impact' not in sample['labels']:
            raise ValueError(f"Sample {idx}: labels must have 'intent' and 'impact' keys")
        
        if not isinstance(sample['labels']['intent'], list):
            raise ValueError(f"Sample {idx}: intent must be list")
        
        if not isinstance(sample['labels']['impact'], list):
            raise ValueError(f"Sample {idx}: impact must be list")


In [4]:
# ============================================================================
# DATA LOADING AND PREPROCESSING
# ============================================================================

class DataProcessor:
    """Handle data loading, validation, and preprocessing."""
    
    def __init__(self, config: ExperimentConfig):
        self.config = config
        self.intent_mlb = MultiLabelBinarizer(classes=config.INTENT_LABELS)
        self.impact_mlb = MultiLabelBinarizer(classes=config.IMPACT_LABELS)
        
    def load_data(self) -> List[Dict]:
        """Load and validate dataset."""
        try:
            with open(self.config.DATASET_PATH, 'r', encoding='utf-8') as f:
                data = json.load(f)
            print(f"Successfully loaded {len(data)} samples from {self.config.DATASET_PATH}")
            
            validate_dataset_structure(data)
            print("Dataset structure validation passed")
            
            return data
            
        except FileNotFoundError:
            raise FileNotFoundError(f"Dataset not found at {self.config.DATASET_PATH}")
        except json.JSONDecodeError as e:
            raise ValueError(f"Invalid JSON format: {e}")
        except Exception as e:
            raise RuntimeError(f"Error loading dataset: {e}")
    
    def prepare_labels(self, data: List[Dict]) -> Tuple[np.ndarray, np.ndarray]:
        """Prepare multi-label encoded arrays."""
        intent_labels = [sample['labels']['intent'] for sample in data]
        impact_labels = [sample['labels']['impact'] for sample in data]
        
        intent_encoded = self.intent_mlb.fit_transform(intent_labels)
        impact_encoded = self.impact_mlb.fit_transform(impact_labels)
        
        print(f"Intent labels shape: {intent_encoded.shape}")
        print(f"Impact labels shape: {impact_encoded.shape}")
        
        return intent_encoded, impact_encoded
    
    def split_data(
        self, 
        data: List[Dict], 
        intent_labels: np.ndarray, 
        impact_labels: np.ndarray
    ) -> Dict[str, Tuple[List[Dict], np.ndarray, np.ndarray]]:
        """Split data into train/val/test sets."""
        
        # First split: train + temp
        train_data, temp_data, train_intent, temp_intent, train_impact, temp_impact = train_test_split(
            data,
            intent_labels,
            impact_labels,
            test_size=(self.config.VAL_SIZE + self.config.TEST_SIZE),
            random_state=self.config.RANDOM_SEED,
            shuffle=True
        )
        
        # Second split: val + test
        val_size_adjusted = self.config.VAL_SIZE / (self.config.VAL_SIZE + self.config.TEST_SIZE)
        val_data, test_data, val_intent, test_intent, val_impact, test_impact = train_test_split(
            temp_data,
            temp_intent,
            temp_impact,
            test_size=(1 - val_size_adjusted),
            random_state=self.config.RANDOM_SEED,
            shuffle=True
        )
        
        splits = {
            'train': (train_data, train_intent, train_impact),
            'val': (val_data, val_intent, val_impact),
            'test': (test_data, test_intent, test_impact)
        }
        
        print(f"Train: {len(train_data)} samples")
        print(f"Val: {len(val_data)} samples")
        print(f"Test: {len(test_data)} samples")
        
        return splits

In [5]:
# ============================================================================
# DATASET CLASS
# ============================================================================

class MultiLabelTextDataset(Dataset):
    """PyTorch Dataset for multi-label text classification."""
    
    def __init__(
        self, 
        texts: List[str], 
        labels: np.ndarray, 
        tokenizer, 
        max_length: int
    ):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length
        
    def __len__(self) -> int:
        return len(self.texts)
    
    def __getitem__(self, idx: int) -> Dict[str, torch.Tensor]:
        text = self.texts[idx]
        label = self.labels[idx]
        
        encoding = self.tokenizer(
            text,
            max_length=self.max_length,
            padding='max_length',
            truncation=True,
            return_tensors='pt'
        )
        
        return {
            'input_ids': encoding['input_ids'].flatten(),
            'attention_mask': encoding['attention_mask'].flatten(),
            'labels': torch.FloatTensor(label)
        }

In [6]:
# ============================================================================
# MODEL WRAPPER FOR SENTENCE TRANSFORMERS
# ============================================================================

class SentenceTransformerClassifier(nn.Module):
    """Wrapper for Sentence Transformer models with classification head."""
    
    def __init__(self, model_name: str, num_labels: int, dropout: float = 0.2):
        super().__init__()
        self.encoder = SentenceTransformer(model_name)
        embedding_dim = self.encoder.get_sentence_embedding_dimension()
        self.dropout = nn.Dropout(dropout)
        self.classifier = nn.Linear(embedding_dim, num_labels)
        
    def forward(self, input_ids, attention_mask):
        # Sentence transformers expect text, not token IDs
        # This will be handled differently in the trainer
        pass

In [7]:
# ============================================================================
# EARLY STOPPING
# ============================================================================

class EarlyStopping:
    """Early stopping to prevent overfitting."""
    
    def __init__(self, patience: int = 3, min_delta: float = 0.0):
        self.patience = patience
        self.min_delta = min_delta
        self.counter = 0
        self.best_loss = None
        self.early_stop = False
        
    def __call__(self, val_loss: float) -> bool:
        if self.best_loss is None:
            self.best_loss = val_loss
        elif val_loss > self.best_loss - self.min_delta:
            self.counter += 1
            if self.counter >= self.patience:
                self.early_stop = True
        else:
            self.best_loss = val_loss
            self.counter = 0
            
        return self.early_stop

In [8]:
# ============================================================================
# METRICS CALCULATOR
# ============================================================================

class MetricsCalculator:
    """Calculate and store evaluation metrics."""
    
    @staticmethod
    def calculate_metrics(
        y_true: np.ndarray, 
        y_pred: np.ndarray, 
        label_names: List[str]
    ) -> Dict[str, float]:
        """Calculate all metrics for multi-label classification."""
        
        metrics = {
            'subset_accuracy': accuracy_score(y_true, y_pred),
            'macro_f1': f1_score(y_true, y_pred, average='macro', zero_division=0),
            'weighted_f1': f1_score(y_true, y_pred, average='weighted', zero_division=0),
            'micro_f1': f1_score(y_true, y_pred, average='micro', zero_division=0),
            'hamming_loss': hamming_loss(y_true, y_pred)
        }
        
        # Per-label metrics
        per_label_f1 = f1_score(y_true, y_pred, average=None, zero_division=0)
        per_label_precision = precision_score(y_true, y_pred, average=None, zero_division=0)
        per_label_recall = recall_score(y_true, y_pred, average=None, zero_division=0)
        
        per_label_metrics = {}
        for i, label in enumerate(label_names):
            per_label_metrics[f'{label}_f1'] = per_label_f1[i]
            per_label_metrics[f'{label}_precision'] = per_label_precision[i]
            per_label_metrics[f'{label}_recall'] = per_label_recall[i]
        
        metrics.update(per_label_metrics)
        
        return metrics

In [9]:
# ============================================================================
# MODEL TRAINER
# ============================================================================

class ModelTrainer:
    """Handle model training and evaluation."""
    
    def __init__(self, config: ExperimentConfig):
        self.config = config
        self.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.use_data_parallel = torch.cuda.device_count() > 1  # ADD THIS LINE
        print(f"Using device: {self.device}")
        if self.use_data_parallel:  # ADD THESE 3 LINES
            print(f"DataParallel enabled with {torch.cuda.device_count()} GPUs")
        else:
            print("Single GPU mode")
        
    def get_model_and_tokenizer(
        self, 
        model_name: str, 
        num_labels: int
    ) -> Tuple[nn.Module, any, int]:
        """Load model and tokenizer with appropriate configuration."""
        
        try:
            # Long-context models
            if 'longformer' in model_name.lower():
                tokenizer = LongformerTokenizer.from_pretrained(model_name)
                model = LongformerForSequenceClassification.from_pretrained(
                    model_name,
                    num_labels=num_labels,
                    problem_type="multi_label_classification",
                    ignore_mismatched_sizes=True
                )
                max_length = self.config.MAX_SEQ_LENGTH_LONG
                
            elif 'bigbird' in model_name.lower():
                tokenizer = BigBirdTokenizer.from_pretrained(model_name)
                model = BigBirdForSequenceClassification.from_pretrained(
                    model_name,
                    num_labels=num_labels,
                    problem_type="multi_label_classification",
                    ignore_mismatched_sizes=True
                )
                max_length = self.config.MAX_SEQ_LENGTH_LONG
                
            # Encoder-decoder models
            elif 'bart' in model_name.lower():
                tokenizer = BartTokenizer.from_pretrained(model_name)
                model = BartForSequenceClassification.from_pretrained(
                    model_name,
                    num_labels=num_labels,
                    problem_type="multi_label_classification",
                    ignore_mismatched_sizes=True
                )
                max_length = self.config.MAX_SEQ_LENGTH_STANDARD

            # LED (Longformer Encoder-Decoder)
            elif 'led' in model_name.lower():
                from transformers import LEDTokenizer, LEDForSequenceClassification
                tokenizer = LEDTokenizer.from_pretrained(model_name)
                
                # LED can be used directly for classification
                try:
                    model = LEDForSequenceClassification.from_pretrained(
                        model_name,
                        num_labels=num_labels,
                        problem_type="multi_label_classification"
                    )
                except:
                    # If classification head doesn't exist, use custom wrapper
                    from transformers import LEDModel
                    base_model = LEDModel.from_pretrained(model_name)
                    
                    class LEDClassifierWrapper(nn.Module):
                        def __init__(self, led_model, num_labels):
                            super().__init__()
                            self.led = led_model
                            self.classifier = nn.Linear(led_model.config.d_model, num_labels)
                            
                        def forward(self, input_ids, attention_mask, **kwargs):
                            # Set global attention on first token
                            global_attention_mask = torch.zeros_like(input_ids)
                            global_attention_mask[:, 0] = 1
                            
                            encoder_outputs = self.led.encoder(
                                input_ids=input_ids,
                                attention_mask=attention_mask,
                                global_attention_mask=global_attention_mask
                            )
                            pooled = encoder_outputs.last_hidden_state[:, 0, :]
                            logits = self.classifier(pooled)
                            
                            from transformers.modeling_outputs import SequenceClassifierOutput
                            return SequenceClassifierOutput(logits=logits)
                    
                    model = LEDClassifierWrapper(base_model, num_labels)
                
                max_length = self.config.MAX_SEQ_LENGTH_LONG  # 1024 for LED

            
                
            elif 't5' in model_name.lower() or 'flan' in model_name.lower() or 'pegasus' in model_name.lower():
                tokenizer = AutoTokenizer.from_pretrained(model_name)
                # Use AutoModelForSeq2SeqLM wrapper for classification
                from transformers import AutoModelForSeq2SeqLM
                base_model = AutoModelForSeq2SeqLM.from_pretrained(model_name)
                
                # Create classification wrapper
                class T5ClassifierWrapper(nn.Module):
                    def __init__(self, t5_model, num_labels):
                        super().__init__()
                        self.t5 = t5_model
                        self.classifier = nn.Linear(t5_model.config.d_model, num_labels)
                        
                    def forward(self, input_ids, attention_mask, **kwargs):
                        encoder_outputs = self.t5.encoder(
                            input_ids=input_ids,
                            attention_mask=attention_mask
                        )
                        pooled = encoder_outputs.last_hidden_state.mean(dim=1)  # Mean pooling
                        logits = self.classifier(pooled)
                        
                        # Return compatible output
                        from transformers.modeling_outputs import SequenceClassifierOutput
                        return SequenceClassifierOutput(logits=logits)
                
                model = T5ClassifierWrapper(base_model, num_labels)
                max_length = self.config.MAX_SEQ_LENGTH_STANDARD
                
            # Sentence transformers
            elif 'sentence-transformers' in model_name:
                # Special handling for sentence transformers
                return None, None, self.config.MAX_SEQ_LENGTH_STANDARD
                
            # Standard transformers
            else:
                tokenizer = AutoTokenizer.from_pretrained(model_name)
                model = AutoModelForSequenceClassification.from_pretrained(
                    model_name,
                    num_labels=num_labels,
                    problem_type="multi_label_classification",
                    ignore_mismatched_sizes=True
                )
                max_length = self.config.MAX_SEQ_LENGTH_STANDARD
            
            model.to(self.device)
            print(f"Successfully loaded {model_name}")
            print(f"Max sequence length: {max_length}")


            if self.use_data_parallel and model is not None:
                model = nn.DataParallel(model, device_ids=[0, 1])
                print(f"Model wrapped in DataParallel")
            
            return model, tokenizer, max_length

            
        except Exception as e:
            raise RuntimeError(f"Failed to load model {model_name}: {str(e)}")


    def train_sentence_transformer_model(
        self,
        model_name: str,
        train_texts: List[str],
        train_labels: np.ndarray,
        val_texts: List[str],
        val_labels: np.ndarray,
        task_name: str
    ) -> Dict[str, float]:
        """
        Special training pipeline for sentence transformer models.
        Uses pre-computed embeddings + classification head.
        """
        print(f"\n{'='*80}")
        print(f"Training {model_name} for {task_name}")
        print(f"{'='*80}")
        
        try:
            from sentence_transformers import SentenceTransformer
            
            # Load sentence transformer
            print(f"Loading sentence transformer: {model_name}")
            encoder = SentenceTransformer(model_name)
            embedding_dim = encoder.get_sentence_embedding_dimension()
            print(f"Embedding dimension: {embedding_dim}")
            
            # Create classification head
            classifier = nn.Sequential(
                nn.Dropout(self.config.DROPOUT),
                nn.Linear(embedding_dim, train_labels.shape[1])
            )
            
            # Wrap in DataParallel if available
            if self.use_data_parallel:
                classifier = nn.DataParallel(classifier, device_ids=[0, 1])
                print("Classifier wrapped in DataParallel")
            
            classifier = classifier.to(self.device)
            
            # Encode all texts (batch processing)
            print("Encoding texts...")
            train_embeddings = encoder.encode(
                train_texts, 
                batch_size=32,
                show_progress_bar=True, 
                convert_to_tensor=True,
                device='cuda'
            )
            val_embeddings = encoder.encode(
                val_texts, 
                batch_size=32,
                show_progress_bar=True, 
                convert_to_tensor=True,
                device='cuda'
            )
            
            # Move to device
            train_embeddings = train_embeddings.to(self.device)
            val_embeddings = val_embeddings.to(self.device)
            train_labels_torch = torch.FloatTensor(train_labels).to(self.device)
            val_labels_torch = torch.FloatTensor(val_labels).to(self.device)
            
            # Setup training
            optimizer = AdamW(
                classifier.parameters(),
                lr=self.config.LEARNING_RATE,
                betas=(self.config.ADAM_BETA1, self.config.ADAM_BETA2),
                eps=self.config.ADAM_EPSILON,
                weight_decay=self.config.WEIGHT_DECAY
            )
            
            total_steps = (len(train_embeddings) // self.config.BATCH_SIZE) * self.config.NUM_EPOCHS
            scheduler = get_linear_schedule_with_warmup(
                optimizer,
                num_warmup_steps=self.config.WARMUP_STEPS,
                num_training_steps=total_steps
            )
            
            criterion = nn.BCEWithLogitsLoss()
            early_stopping = EarlyStopping(patience=self.config.EARLY_STOPPING_PATIENCE)
            
            best_val_loss = float('inf')
            
            # Training loop
            for epoch in range(self.config.NUM_EPOCHS):
                print(f"\nEpoch {epoch + 1}/{self.config.NUM_EPOCHS}")
                
                # Train
                classifier.train()
                total_loss = 0
                num_batches = 0
                
                progress_bar = tqdm(
                    range(0, len(train_embeddings), self.config.BATCH_SIZE),
                    desc="Training",
                    leave=False
                )
                
                for i in progress_bar:
                    batch_embeddings = train_embeddings[i:i+self.config.BATCH_SIZE]
                    batch_labels = train_labels_torch[i:i+self.config.BATCH_SIZE]
                    
                    optimizer.zero_grad()
                    logits = classifier(batch_embeddings)
                    loss = criterion(logits, batch_labels)
                    loss.backward()
                    
                    torch.nn.utils.clip_grad_norm_(classifier.parameters(), self.config.MAX_GRAD_NORM)
                    optimizer.step()
                    scheduler.step()
                    
                    total_loss += loss.item()
                    num_batches += 1
                    progress_bar.set_postfix({'loss': loss.item()})
                
                train_loss = total_loss / num_batches
                
                # Validate
                classifier.eval()
                with torch.no_grad():
                    val_logits = classifier(val_embeddings)
                    val_loss = criterion(val_logits, val_labels_torch).item()
                    val_preds = (torch.sigmoid(val_logits) > 0.5).cpu().numpy()
                
                print(f"Train Loss: {train_loss:.4f} | Val Loss: {val_loss:.4f}")
                
                if early_stopping(val_loss):
                    print(f"Early stopping triggered at epoch {epoch + 1}")
                    break
                
                if val_loss < best_val_loss:
                    best_val_loss = val_loss
            
            print(f"\nTraining completed for {model_name}")
            print(f"Best validation loss: {best_val_loss:.4f}")
            
            # Calculate metrics
            metrics = MetricsCalculator.calculate_metrics(
                val_labels,
                val_preds,
                self.config.INTENT_LABELS if 'intent' in task_name.lower() 
                else self.config.IMPACT_LABELS
            )
            
            # Clean up
            del encoder
            del classifier
            del train_embeddings
            del val_embeddings
            clear_memory()
            
            return metrics
            
        except Exception as e:
            print(f"\n{'!'*80}")
            print(f"TRAINING FAILED for {model_name}")
            print(f"{'!'*80}")
            print(f"Error: {str(e)}")
            clear_memory()
            return None    
    
    def train_epoch(
        self, 
        model: nn.Module, 
        dataloader: DataLoader, 
        optimizer: torch.optim.Optimizer,
        scheduler,
        criterion: nn.Module
    ) -> float:
        """Train for one epoch."""
        model.train()
        total_loss = 0
        
        progress_bar = tqdm(dataloader, desc="Training", leave=False)
        
        for batch in progress_bar:
            try:
                input_ids = batch['input_ids'].to(self.device)
                attention_mask = batch['attention_mask'].to(self.device)
                labels = batch['labels'].to(self.device)
                
                optimizer.zero_grad()
                
                outputs = model(
                    input_ids=input_ids,
                    attention_mask=attention_mask
                )
                
                logits = outputs.logits if hasattr(outputs, 'logits') else outputs[0]
                loss = criterion(logits, labels)
                
                loss.backward()
                torch.nn.utils.clip_grad_norm_(model.parameters(), self.config.MAX_GRAD_NORM)
                optimizer.step()
                scheduler.step()
                
                total_loss += loss.item()
                progress_bar.set_postfix({'loss': loss.item()})
                
            except RuntimeError as e:
                if "out of memory" in str(e):
                    raise MemoryError(f"OOM Error during training: {str(e)}")
                else:
                    raise RuntimeError(f"Training error: {str(e)}")
        
        return total_loss / len(dataloader)
    
    def evaluate(
        self, 
        model: nn.Module, 
        dataloader: DataLoader, 
        criterion: nn.Module
    ) -> Tuple[float, np.ndarray, np.ndarray]:
        """Evaluate model on validation/test set."""
        model.eval()
        total_loss = 0
        all_preds = []
        all_labels = []
        
        progress_bar = tqdm(dataloader, desc="Evaluating", leave=False)
        
        with torch.no_grad():
            for batch in progress_bar:
                try:
                    input_ids = batch['input_ids'].to(self.device)
                    attention_mask = batch['attention_mask'].to(self.device)
                    labels = batch['labels'].to(self.device)
                    
                    outputs = model(
                        input_ids=input_ids,
                        attention_mask=attention_mask
                    )
                    
                    logits = outputs.logits if hasattr(outputs, 'logits') else outputs[0]
                    loss = criterion(logits, labels)
                    
                    total_loss += loss.item()
                    
                    # Convert logits to predictions (threshold at 0.5)
                    preds = torch.sigmoid(logits) > 0.5
                    
                    all_preds.append(preds.cpu().numpy())
                    all_labels.append(labels.cpu().numpy())
                    
                except RuntimeError as e:
                    if "out of memory" in str(e):
                        raise MemoryError(f"OOM Error during evaluation: {str(e)}")
                    else:
                        raise RuntimeError(f"Evaluation error: {str(e)}")
        
        all_preds = np.vstack(all_preds)
        all_labels = np.vstack(all_labels)
        
        return total_loss / len(dataloader), all_preds, all_labels
    
    def train_model(
        self,
        model_name: str,
        train_texts: List[str],
        train_labels: np.ndarray,
        val_texts: List[str],
        val_labels: np.ndarray,
        task_name: str
    ) -> Dict[str, float]:
        """Complete training pipeline for a single model."""
        
        print(f"\n{'='*80}")
        print(f"Training {model_name} for {task_name}")
        print(f"{'='*80}")
        
        try:
            # Get model and tokenizer
            model, tokenizer, max_length = self.get_model_and_tokenizer(
                model_name, 
                train_labels.shape[1]
            )
            
            # Create datasets
            train_dataset = MultiLabelTextDataset(
                train_texts, train_labels, tokenizer, max_length
            )
            val_dataset = MultiLabelTextDataset(
                val_texts, val_labels, tokenizer, max_length
            )
            
            train_loader = DataLoader(
                train_dataset, 
                batch_size=self.config.BATCH_SIZE, 
                shuffle=True
            )
            val_loader = DataLoader(
                val_dataset, 
                batch_size=self.config.BATCH_SIZE, 
                shuffle=False
            )
            
            # Setup optimizer and scheduler
            optimizer = AdamW(
                model.parameters(),
                lr=self.config.LEARNING_RATE,
                betas=(self.config.ADAM_BETA1, self.config.ADAM_BETA2),
                eps=self.config.ADAM_EPSILON,
                weight_decay=self.config.WEIGHT_DECAY
            )
            
            total_steps = len(train_loader) * self.config.NUM_EPOCHS
            scheduler = get_linear_schedule_with_warmup(
                optimizer,
                num_warmup_steps=self.config.WARMUP_STEPS,
                num_training_steps=total_steps
            )
            
            criterion = nn.BCEWithLogitsLoss()
            early_stopping = EarlyStopping(patience=self.config.EARLY_STOPPING_PATIENCE)
            
            # Training loop
            best_val_loss = float('inf')
            
            for epoch in range(self.config.NUM_EPOCHS):
                print(f"\nEpoch {epoch + 1}/{self.config.NUM_EPOCHS}")
                
                train_loss = self.train_epoch(
                    model, train_loader, optimizer, scheduler, criterion
                )
                val_loss, val_preds, val_labels_actual = self.evaluate(
                    model, val_loader, criterion
                )
                
                print(f"Train Loss: {train_loss:.4f} | Val Loss: {val_loss:.4f}")
                
                if early_stopping(val_loss):
                    print(f"Early stopping triggered at epoch {epoch + 1}")
                    break
                
                if val_loss < best_val_loss:
                    best_val_loss = val_loss
            
            print(f"\nTraining completed for {model_name}")
            print(f"Best validation loss: {best_val_loss:.4f}")
            
            # Final metrics (return validation metrics)
            metrics = MetricsCalculator.calculate_metrics(
                val_labels_actual,
                val_preds,
                self.config.INTENT_LABELS if 'intent' in task_name.lower() 
                else self.config.IMPACT_LABELS
            )
            
            # Clean up
            del model
            del tokenizer
            del optimizer
            del scheduler
            clear_memory()
            
            return metrics
            
        except MemoryError as e:
            print(f"\n{'!'*80}")
            print(f"OUT OF MEMORY ERROR for {model_name}")
            print(f"{'!'*80}")
            print(f"Error: {str(e)}")
            print("Consider:")
            print("- Reducing batch size")
            print("- Using a smaller model variant")
            print("- Using gradient accumulation")
            clear_memory()
            return None
            
        except Exception as e:
            print(f"\n{'!'*80}")
            print(f"TRAINING FAILED for {model_name}")
            print(f"{'!'*80}")
            print(f"Error: {str(e)}")
            clear_memory()
            return None

In [10]:
# ============================================================================
# T5 CLASSIFICATION WRAPPER
# ============================================================================

class T5ClassificationWrapper(nn.Module):
    """Wrapper for T5 models to enable classification."""
    
    def __init__(self, t5_model, num_labels: int):
        super().__init__()
        self.t5 = t5_model
        self.classifier = nn.Linear(t5_model.config.d_model, num_labels)
        
    def forward(self, input_ids, attention_mask):
        encoder_outputs = self.t5.encoder(
            input_ids=input_ids,
            attention_mask=attention_mask
        )
        hidden_states = encoder_outputs.last_hidden_state
        pooled = hidden_states[:, 0, :]  # Use first token
        logits = self.classifier(pooled)
        
        # Return in same format as other models
        from transformers.modeling_outputs import SequenceClassifierOutput
        return SequenceClassifierOutput(logits=logits)

In [11]:
# ============================================================================
# EXPERIMENT RUNNER
# ============================================================================

class ExperimentRunner:
    """Orchestrate the complete experiment."""
    
    def __init__(self, config: ExperimentConfig):
        self.config = config
        self.processor = DataProcessor(config)
        self.trainer = ModelTrainer(config)
        self.results = {
            'intent': [],
            'impact': []
        }
        
    def get_model_list(self) -> List[Tuple[str, str, str]]:

        models = [
            ("BERT-base", "Encoder", "bert-base-uncased"),
            ("FinBERT", "Encoder (Domain)", "ProsusAI/finbert"),
            ("RoBERTa-base", "Encoder", "roberta-base"),
            ("FinBERT-Tone", "Encoder (Domain)", "yiyanghkust/finbert-tone"),
            ("FinBERT-ESG", "Encoder (Domain)", "yiyanghkust/finbert-esg"),
            ("SecBERT", "Encoder (Domain)", "nlpaueb/sec-bert-base"),  # NEW
            ("DistilRoBERTa", "Encoder (Light)", "distilroberta-base"),  # NEW
            ("DistilBERT", "Encoder (Light)", "distilbert-base-uncased"),
            ("DeBERTa-v3-small", "Advanced Encoder", "microsoft/deberta-v3-small"),
            ("ELECTRA-small", "Advanced Encoder", "google/electra-small-discriminator"),
            ("ELECTRA-base", "Advanced Encoder", "google/electra-base-discriminator"),
            ("ALBERT-base-v2", "Advanced Encoder", "albert-base-v2"),
            ("XLNet-base", "Advanced Encoder", "xlnet-base-cased"),
            ("BART-base", "Encoder-Decoder", "facebook/bart-base"),
            ("DistilBART-cnn", "Encoder-Decoder (Light)", "sshleifer/distilbart-cnn-6-6"),
        ]

        return models

    def save_label_distribution(self, splits):
        """Save label distribution statistics for train/val/test splits."""
        
        # Extract data from splits
        train_data, train_intent, train_impact = splits['train']
        val_data, val_intent, val_impact = splits['val']
        test_data, test_intent, test_impact = splits['test']
        
        # Calculate intent label distribution
        intent_dist = []
        for i, label in enumerate(self.config.INTENT_LABELS):
            intent_dist.append({
                'Label': label,
                'Train': train_intent[:, i].sum(),
                'Val': val_intent[:, i].sum(),
                'Test': test_intent[:, i].sum(),
                'Total': train_intent[:, i].sum() + val_intent[:, i].sum() + test_intent[:, i].sum()
            })
        
        # Calculate impact label distribution
        impact_dist = []
        for i, label in enumerate(self.config.IMPACT_LABELS):
            impact_dist.append({
                'Label': label,
                'Train': train_impact[:, i].sum(),
                'Val': val_impact[:, i].sum(),
                'Test': test_impact[:, i].sum(),
                'Total': train_impact[:, i].sum() + val_impact[:, i].sum() + test_impact[:, i].sum()
            })
        
        # Create DataFrames
        intent_dist_df = pd.DataFrame(intent_dist)
        impact_dist_df = pd.DataFrame(impact_dist)
        
        # Save to CSV
        os.makedirs(self.config.OUTPUT_DIR, exist_ok=True)
        
        intent_dist_path = os.path.join(self.config.OUTPUT_DIR, 'project2_intent_label_distribution.csv')
        impact_dist_path = os.path.join(self.config.OUTPUT_DIR, 'project2_impact_label_distribution.csv')
        
        intent_dist_df.to_csv(intent_dist_path, index=False)
        impact_dist_df.to_csv(impact_dist_path, index=False)
        
        print(f"Saved: {intent_dist_path}")
        print(f"Saved: {impact_dist_path}")
        
        # Print summary
        print("\n" + "="*80)
        print("INTENT LABEL DISTRIBUTION")
        print("="*80)
        print(intent_dist_df.to_string(index=False))
        
        print("\n" + "="*80)
        print("IMPACT LABEL DISTRIBUTION")
        print("="*80)
        print(impact_dist_df.to_string(index=False))

    
    def run_experiments(self):
        """Run all experiments."""
        
        print("\n" + "="*80)
        print("STARTING EXPERIMENT: Project 2 - Financial Distress Classification")  # CHANGED
        print("="*80)
        
        # Load and prepare data
        print("\n[1/5] Loading dataset...")
        data = self.processor.load_data()
        
        print("\n[2/5] Preparing labels...")
        intent_labels, impact_labels = self.processor.prepare_labels(data)
        
        print("\n[3/5] Splitting data...")
        splits = self.processor.split_data(data, intent_labels, impact_labels)

        # Save label distribution
        self.save_label_distribution(splits)
        
        train_data, train_intent, train_impact = splits['train']
        val_data, val_intent, val_impact = splits['val']
        test_data, test_intent, test_impact = splits['test']
        
        train_texts = [s['text'] for s in train_data]
        val_texts = [s['text'] for s in val_data]
        test_texts = [s['text'] for s in test_data]
        
        # Get model list
        models = self.get_model_list()
        
        print(f"\n[4/5] Training {len(models)} models on 2 tasks...")
        print(f"Total training runs: {len(models) * 2}")
        
           
        # Train all models
        for idx, (model_name, model_type, hf_id) in enumerate(models, 1):
            print(f"\n{'#'*80}")
            print(f"MODEL {idx}/{len(models)}: {model_name} ({model_type})")
            print(f"{'#'*80}")
            
            # Check if sentence transformer
            if 'sentence-transformers' in hf_id:
                # Use special training method for sentence transformers
                intent_metrics = self.trainer.train_sentence_transformer_model(
                    hf_id,
                    train_texts,
                    train_intent,
                    val_texts,
                    val_intent,
                    "Intent Classification"
                )
                
                if intent_metrics is not None:
                    intent_metrics['model_name'] = model_name
                    intent_metrics['model_type'] = model_type
                    intent_metrics['hf_id'] = hf_id
                    self.results['intent'].append(intent_metrics)
                
                impact_metrics = self.trainer.train_sentence_transformer_model(
                    hf_id,
                    train_texts,
                    train_impact,
                    val_texts,
                    val_impact,
                    "Impact Classification"
                )
                
                if impact_metrics is not None:
                    impact_metrics['model_name'] = model_name
                    impact_metrics['model_type'] = model_type
                    impact_metrics['hf_id'] = hf_id
                    self.results['impact'].append(impact_metrics)
            else:
                # Normal training for non-sentence-transformer models
                intent_metrics = self.trainer.train_model(
                    hf_id,
                    train_texts,
                    train_intent,
                    val_texts,
                    val_intent,
                    "Intent Classification"
                )
                
                if intent_metrics is not None:
                    intent_metrics['model_name'] = model_name
                    intent_metrics['model_type'] = model_type
                    intent_metrics['hf_id'] = hf_id
                    self.results['intent'].append(intent_metrics)
                
                impact_metrics = self.trainer.train_model(
                    hf_id,
                    train_texts,
                    train_impact,
                    val_texts,
                    val_impact,
                    "Impact Classification"
                )
                
                if impact_metrics is not None:
                    impact_metrics['model_name'] = model_name
                    impact_metrics['model_type'] = model_type
                    impact_metrics['hf_id'] = hf_id
                    self.results['impact'].append(impact_metrics)
        
        print("\n[5/5] Saving results...")
        self.save_results()
        
        print("\n" + "="*80)
        print("EXPERIMENT COMPLETED")
        print("="*80)

    def save_results(self):
        """Save all results to CSV files."""
        
        os.makedirs(self.config.OUTPUT_DIR, exist_ok=True)
        
        # Main results
        intent_df = pd.DataFrame(self.results['intent'])
        impact_df = pd.DataFrame(self.results['impact'])
        
        # Reorder columns for main metrics
        main_cols = ['model_name', 'model_type', 'subset_accuracy', 'macro_f1', 
                     'weighted_f1', 'micro_f1', 'hamming_loss']
        
        intent_main = intent_df[main_cols]
        impact_main = impact_df[main_cols]
        
        # Save main results - CHANGED FILENAMES
        intent_main_path = os.path.join(self.config.OUTPUT_DIR, 'project2_intent_results.csv')
        impact_main_path = os.path.join(self.config.OUTPUT_DIR, 'project2_impact_results.csv')
        
        intent_main.to_csv(intent_main_path, index=False)
        impact_main.to_csv(impact_main_path, index=False)
        
        print(f"Saved: {intent_main_path}")
        print(f"Saved: {impact_main_path}")
        
        # Per-label results
        intent_label_cols = ['model_name', 'model_type'] + \
                           [col for col in intent_df.columns if any(label in col for label in self.config.INTENT_LABELS)]
        impact_label_cols = ['model_name', 'model_type'] + \
                           [col for col in impact_df.columns if any(label in col for label in self.config.IMPACT_LABELS)]
        
        intent_per_label = intent_df[intent_label_cols]
        impact_per_label = impact_df[impact_label_cols]
        
        # CHANGED FILENAMES
        intent_per_label_path = os.path.join(self.config.OUTPUT_DIR, 'project2_intent_per_label.csv')
        impact_per_label_path = os.path.join(self.config.OUTPUT_DIR, 'project2_impact_per_label.csv')
        
        intent_per_label.to_csv(intent_per_label_path, index=False)
        impact_per_label.to_csv(impact_per_label_path, index=False)
        
        print(f"Saved: {intent_per_label_path}")
        print(f"Saved: {impact_per_label_path}")

In [12]:
# ============================================================================
# MAIN EXECUTION
# ============================================================================
    
# Set seed for reproducibility
set_seed(CONFIG.RANDOM_SEED)

# Initialize and run experiment
runner = ExperimentRunner(CONFIG)
runner.run_experiments()

print("\n" + "="*80)
print("All results saved to:", CONFIG.OUTPUT_DIR)
print("="*80)

Using device: cuda
DataParallel enabled with 2 GPUs

STARTING EXPERIMENT: Project 2 - Financial Distress Classification

[1/5] Loading dataset...
Successfully loaded 2408 samples from /kaggle/input/eacl-26-dataset-2/EACL_26-FinancialDiscussionsDataset.json
Dataset structure validation passed

[2/5] Preparing labels...
Intent labels shape: (2408, 7)
Impact labels shape: (2408, 6)

[3/5] Splitting data...
Train: 1444 samples
Val: 482 samples
Test: 482 samples
Saved: /kaggle/working/project2_intent_label_distribution.csv
Saved: /kaggle/working/project2_impact_label_distribution.csv

INTENT LABEL DISTRIBUTION
                                  Label  Train  Val  Test  Total
                     Advocacy & Warning    369  129   113    611
Community Building & Solidarity Seeking    385  136   122    643
     Emotional & Esteem Support-Seeking    459  146   162    767
             Informational Help-Seeking    488  148   160    796
              Instrumental Help-Seeking    302  115    98    5

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

...

Evaluating:   0%|          | 0/31 [00:00<?, ?it/s]

Train Loss: 0.1840 | Val Loss: 0.3444

Epoch 6/10


Training:   0%|          | 0/91 [00:00<?, ?it/s]

Evaluating:   0%|          | 0/31 [00:00<?, ?it/s]

Train Loss: 0.1360 | Val Loss: 0.3813
Early stopping triggered at epoch 6

Training completed for sshleifer/distilbart-cnn-6-6
Best validation loss: 0.3135

[5/5] Saving results...
Saved: /kaggle/working/project2_intent_results.csv
Saved: /kaggle/working/project2_impact_results.csv
Saved: /kaggle/working/project2_intent_per_label.csv
Saved: /kaggle/working/project2_impact_per_label.csv

EXPERIMENT COMPLETED

All results saved to: /kaggle/working
